<a href="https://colab.research.google.com/github/unt-iialab/INFO5731_Spring2020/blob/master/Assignments/INFO5731_Assignment_Two.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**

(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [2019 Dell labtop](https://www.amazon.com/Dell-Inspiron-5000-5570-Laptop/dp/B07N49F51N/ref=sr_1_11?crid=1IJ7UWF2F4GHH&keywords=dell%2Bxps%2B15&qid=1580173569&sprefix=dell%2Caps%2C181&sr=8-11&th=1) on amazon.

(2) Collect the top 100 User Reviews of the film [Joker](https://www.imdb.com/title/tt7286456/reviews?ref_=tt_urv) from IMDB.

(3) Collect the abstracts of the top 100 research papers by using the query [natural language processing](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(4) Collect the top 100 tweets by using hashtag ["#CovidVaccine"](https://twitter.com/hashtag/CovidVaccine) from Twitter. 


In [93]:
from bs4 import BeautifulSoup
import requests
import urllib
import csv

results_file_path = 'citeseerx_results.csv'

# Initialize query ULR and parameters
citeseerx_query_url = 'https://citeseerx.ist.psu.edu/search'
citeseerx_result_url = 'https://citeseerx.ist.psu.edu'
q = 'natural language processing'
sort = 'rlv'
t = 'doc'

# Retrieve query results
results = []
# Query loop to return 100 results, 10 at a time
# temp for testing
for i in range(0,100, 10):
#for i in range(0,10, 10):
  #print(i)
  params = {'q': q, 'sort': sort, 't': t, 'start': i}
  #print(params)
  response = requests.get(citeseerx_query_url, params=params)
  print(f'URL: {response.url}, start: {i}')
  response_html = response.text
  response_soup = BeautifulSoup(response_html, 'html.parser')
  for div in response_soup.find_all('div', class_='result'):
    for link in div.find_all('a', class_='doc_details'):
      result_relative_url = link.get('href')
      #print(result_relative_url)
      result_url = citeseerx_result_url + result_relative_url
      #result_urls.append(result_url)
      #print(result_url)
      results.append({'url':result_url})

print(f'Retrieved {len(results)} results.')
print('Retrieving results details...')

# Get details of each result
for result in results:
  result_response = requests.get(result['url'])
  result_html = result_response.text
  result_soup = BeautifulSoup(result_html, 'html.parser')
  abstract_block = result_soup.find('div', id='abstract')
  try:
    abstract = abstract_block.p.text
  except AttributeError:
    print('AttributeError:', abstract_block)
    abstract = ''
  
  result['abstract'] = abstract

# Save results
with open(results_file_path, 'w') as results_file:
  fieldnames = ['url', 'abstract']
  results_writer = csv.DictWriter(results_file, fieldnames=fieldnames)
  results_writer.writeheader()
  for result in results:
    results_writer.writerow(result)

print(f'Result data saved to {results_file_path}')

URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=0, start: 0
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=10, start: 10
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=20, start: 20
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=30, start: 30
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=40, start: 40
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=50, start: 50
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=60, start: 60
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=70, start: 70
URL: https://citeseerx.ist.psu.edu/search?q=natural+language+processing&sort=rlv&t=doc&start=80, start: 80
URL: https://citeseerx.ist.psu.edu/sear

# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:

(1) Remove noise, such as special characters and punctuations.

(2) Remove numbers.

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

(4) Lowercase all texts

(5) Stemming. 

(6) Lemmatization.

In [94]:
import string
import csv
# Import and download all needed NLTK modules and data
import nltk
from nltk.corpus import PlaintextCorpusReader
from nltk.corpus import stopwords
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [97]:
from nltk.stem import PorterStemmer
from textblob import Word # for lemmatization

data_file_path = 'citeseerx_results.csv'
cleaned = []
with open(data_file_path, 'r') as data_file:
  reader = csv.DictReader(data_file)
  for row in reader:
    words = nltk.word_tokenize(row['abstract'])
    sentences = nltk.sent_tokenize(row['abstract'])

    # lowercase
    lowered = []
    sentences_lowered = []
    for sent in sentences:
      sent_lowered = []
      words = nltk.word_tokenize(sent)
      for word in words:
        sent_lowered.append(word.lower())        
      #print(' '.join(sent_lowered))
      sentences_lowered.append(sent_lowered)
    #print(sentences_lowered)

    # remove punctuation
    # make translation for punctuation
    remove_punctuation = str.maketrans(string.punctuation, ' '*len(string.punctuation))
    no_punc_sentences = []
    for sent in sentences_lowered:
      no_punc_sent = []
      for word in sent:
        no_punc_word = word.translate(remove_punctuation)
        if not no_punc_word.isspace():
          no_punc_sent.append(no_punc_word)
      #print(no_punc_sent)
      no_punc_sentences.append(no_punc_sent)
    #print(no_punc_sentences)

    # remove numbers
    no_digits = []
    remove_digits = str.maketrans(string.digits, ' '*len(string.digits))
    no_digits_sentences = []
    for sent in no_punc_sentences:
      no_digit_sent = []
      for word in sent:
        word_no_digits = word.translate(remove_digits)
        if not word_no_digits.isspace():
          no_digit_sent.append(word_no_digits)
      no_digits_sentences.append(no_digit_sent)
    #print(no_digits_sentences)

    # remove stopwords
    stop = stopwords.words('english')
    no_stops_sentences = []
    for sent in no_digits_sentences:
      no_stop_sent = []
      for word in sent:
        if word not in stop:
          no_stop_sent.append(word)
      no_stops_sentences.append(no_stop_sent)
    #print(no_stops_sentences)

    # lemmatize
    #st = PorterStemmer()
    lemmed_sentences = []
    for sent in no_stops_sentences:
      lemmed_sent = []
      for word in sent:
        #lemmed.append(st.stem(Word(word).lemmatize()))
        lemmed_sent.append(Word(word).lemmatize())
      lemmed_sentences.append(lemmed_sent)
    #print(lemmed_sentences)
    cleaned.append(lemmed_sentences)

# Cleaned results
print('Cleaned results:')
for sent in cleaned:
  print(sent)

#write to CSV
with open('citeseerx_results_cleaned.csv', 'w') as csv_out:
  csv_writer = csv.writer(csv_out)
  for doc in cleaned:
    csv_writer.writerow(doc)



Cleaned results:
[]
[['concept', 'maximum', 'entropy', 'traced', 'back', 'along', 'multiple', 'thread', 'biblical', 'time'], ['recently', 'however', 'computer', 'become', 'powerful', 'enough', 'permit', 'widescale', 'application', 'concept', 'real', 'world', 'problem', 'statistical', 'estimation', 'pattern', 'recognition'], ['paper', 'describe', 'method', 'statistical', 'modeling', 'based', 'maximum', 'entropy'], ['present', 'maximum likelihood', 'approach', 'automatically', 'constructing', 'maximum', 'entropy', 'model', 'describe', 'implement', 'approach', 'efficiently', 'using', 'example', 'several', 'problem', 'natural', 'language', 'processing']]
[['scaling', 'conditional', 'random', 'field', 'natural', 'language', 'processing', 'term', 'condition', 'term', 'condition', 'copyright', 'work', 'deposited', 'minerva', 'access', 'retained']]
[['paper', 'address', 'issue', 'cooperation', 'linguistics', 'natural', 'language', 'processing', 'nlp', 'general', 'linguistics', 'machine', 'tran

# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [108]:
# Write your code here
nltk.download('averaged_perceptron_tagger')

#3.1 - POS
tag_count = {}
for doc in cleaned:
  #print(doc)
  #nltk.pos_tag(text)
  
  for sent in doc:
    sent_tagged = nltk.pos_tag(sent)
    print(sent_tagged)
    for tag in sent_tagged:
      #print(tag[1])
      count = tag_count.get(tag[1],0)
      count += 1
      tag_count[tag[1]] = count

#count N, V, Adj, Adv
for tag in tag_count:
  print(tag, '-', tag_count[tag])





[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[('concept', 'NN'), ('maximum', 'JJ'), ('entropy', 'NN'), ('traced', 'VBD'), ('back', 'RB'), ('along', 'RB'), ('multiple', 'JJ'), ('thread', 'JJ'), ('biblical', 'JJ'), ('time', 'NN')]
[('recently', 'RB'), ('however', 'RB'), ('computer', 'NN'), ('become', 'VBP'), ('powerful', 'JJ'), ('enough', 'JJ'), ('permit', 'NN'), ('widescale', 'JJ'), ('application', 'NN'), ('concept', 'NN'), ('real', 'JJ'), ('world', 'NN'), ('problem', 'NN'), ('statistical', 'JJ'), ('estimation', 'NN'), ('pattern', 'NN'), ('recognition', 'NN')]
[('paper', 'NN'), ('describe', 'NN'), ('method', 'NN'), ('statistical', 'JJ'), ('modeling', 'NN'), ('based', 'VBN'), ('maximum', 'JJ'), ('entropy', 'NN')]
[('present', 'JJ'), ('maximum likelihood', 'NN'), ('approach', 'NN'), ('automatically', 'RB'), ('constructing', 'VBG'), ('maximum', 'JJ'

In [109]:
#3.1 - Constituency Parsing and Dependency Parsing
print('3.1 - Constituency Parsing and Dependency Parsing')
import spacy
from spacy import displacy
nlp=spacy.load('en_core_web_sm')
for doc in cleaned:
  for sent in doc:
    print(sent)
    # convert sent to string
    phrase = ' '.join(sent)
    displacy.render(nlp(phrase),jupyter=True)

3.1 - Constituency Parsing and Dependency Parsing
['concept', 'maximum', 'entropy', 'traced', 'back', 'along', 'multiple', 'thread', 'biblical', 'time']


['recently', 'however', 'computer', 'become', 'powerful', 'enough', 'permit', 'widescale', 'application', 'concept', 'real', 'world', 'problem', 'statistical', 'estimation', 'pattern', 'recognition']


['paper', 'describe', 'method', 'statistical', 'modeling', 'based', 'maximum', 'entropy']


['present', 'maximum likelihood', 'approach', 'automatically', 'constructing', 'maximum', 'entropy', 'model', 'describe', 'implement', 'approach', 'efficiently', 'using', 'example', 'several', 'problem', 'natural', 'language', 'processing']


['scaling', 'conditional', 'random', 'field', 'natural', 'language', 'processing', 'term', 'condition', 'term', 'condition', 'copyright', 'work', 'deposited', 'minerva', 'access', 'retained']


...

['logic', 'limitation', 'program', 'also', 'discussed']


[]


['summarize', 'experience', 'using', 'framenet', 'two', 'rather', 'different', 'project', 'natural', 'language', 'processing', 'nlp']


['conclude', 'nlp', 'benefit', 'framenet', 'different', 'way', 'sketch', 'problem', 'need', 'overcome']


[]


In [110]:
# Constiuency parsing - install and import
!pip install benepar
import benepar
benepar.download('benepar_en3')

[nltk_data] Downloading package benepar_en3 to /root/nltk_data...
[nltk_data]   Package benepar_en3 is already up-to-date!


True

In [111]:
# Constiuency parsing
parser = benepar.Parser("benepar_en3")
for doc in cleaned:
  for sent in doc:
    input_sentence = benepar.InputSentence(words=sent,)
    print(input_sentence)
    try:
      tree = parser.parse(input_sentence)
      print(tree)
    except RuntimeError:
      print('RuntimeError - input_sentence:', input_sentence)


Streaming output truncated to the last 5000 lines.
      (VBD emerged)
      (NP
        (NP (JJ new) (NN area))
        (NP (NML (NN machine) (NN learning)) (NN research))))))
InputSentence(words=['try', 'mimic', 'human', 'brain', 'capable', 'processing', 'learning', 'complex', 'input', 'data', 'solving', 'different', 'kind', 'complicated', 'task', 'well'], space_after=None, tags=None, escaped_words=None)
(TOP
  (S
    (VP
      (VB try)
      (PP
        (NP (VB mimic) (NP (JJ human) (NN brain)))
        (ADJP
          (JJ capable)
          (S
            (VP
              (S
                (VP
                  (VBG processing)
                  (NP
                    (VBG learning)
                    (NP (JJ complex) (NN input) (NNS data)))
                  (VBG solving)
                  (NP
                    (NP (JJ different) (NN kind))
                    (VBN complicated)
                    (NN task))))
              (ADVP (RB well)))))))))
InputSentence(words=['succe

In [112]:
# 3.3 Named Entity Recognition
# Entities
nlp = spacy.load('en_core_web_sm') 

entities = {}
for doc in cleaned:
  print(doc)
  for sent in doc:
    phrase = ' '.join(sent)
    #print(phrase)
    x = nlp(phrase) 
    for ent in x.ents:  
        print(ent.text, ent.label_)
        entity_count = entities.get(ent.text, 0)
        entity_count += 1
        entities[ent.text] = entity_count


# Entity count
print('Entity count:')
for key in entities:
  print(key, '-', entities[key])


[]
[['concept', 'maximum', 'entropy', 'traced', 'back', 'along', 'multiple', 'thread', 'biblical', 'time'], ['recently', 'however', 'computer', 'become', 'powerful', 'enough', 'permit', 'widescale', 'application', 'concept', 'real', 'world', 'problem', 'statistical', 'estimation', 'pattern', 'recognition'], ['paper', 'describe', 'method', 'statistical', 'modeling', 'based', 'maximum', 'entropy'], ['present', 'maximum likelihood', 'approach', 'automatically', 'constructing', 'maximum', 'entropy', 'model', 'describe', 'implement', 'approach', 'efficiently', 'using', 'example', 'several', 'problem', 'natural', 'language', 'processing']]
[['scaling', 'conditional', 'random', 'field', 'natural', 'language', 'processing', 'term', 'condition', 'term', 'condition', 'copyright', 'work', 'deposited', 'minerva', 'access', 'retained']]
minerva PERSON
[['paper', 'address', 'issue', 'cooperation', 'linguistics', 'natural', 'language', 'processing', 'nlp', 'general', 'linguistics', 'machine', 'transl

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 

In [ ]:
'''
Write your explanations of the constituency parsing tree and dependency parsing tree here
The constituency parsing tree and dependency parsing trees represet the syntax structure of the input text. The trees indicate both the part of speech
for each token and the relationship of each token to the others. This information is derived from the sequence of the input tokens and the grammar
model used for parsing and extracting the syntax relationships.

'''